In [ ]:
from result_parser import Result
from matplotlib import pyplot as plt
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

result = Result("./result.json")

print(result)

In [ ]:
@interact(sort_key=widgets.Dropdown(
    options=['avg', 'var'],
    value='avg',
    description='Sort by:',
    disabled=False,
))
def plot(sort_key):
    sat_tests = sorted(
        result.get_all_measuements_of_type("SAT", succeeding=True),
        key=lambda m: getattr(m, sort_key),
    )
    units = [test.unit for test in sat_tests]
    assert all((unit == units[0] for unit in units))
    unit = units[0]

    plt.rcParams["figure.figsize"] = 15, 15

    fig, ax = plt.subplots()
    barh = ax.barh(
        [test.combination for test in sat_tests],
        [test.avg for test in sat_tests],
    #     xerr=[test.var for test in sat_tests],
        align="center",
        color=["#3465A4" if test.server.name == test.client.name else "#888" for test in sat_tests],
    )
    ax.errorbar(
        x=[test.avg for test in sat_tests],
        y=[test.combination for test in sat_tests],
        xerr=[test.var for test in sat_tests],
        lw = 2,
        capsize=4,
        capthick=4,
        color="red",
        fmt="none",
    )
    ax.bar_label(
        container=barh,
        labels=[test.details for test in sat_tests],
        color="#fff",
        label_type="center",
    )

    ax.set_xlabel(f"Goodput ({unit})")
    ax.set_title("SAT Goodput Measurement Results of Succeeding Combinations")
    ax.xaxis.grid(True)
    plt.show()